In [ ]:
import agh_db_lectures
agh_db_lectures.prepare_notebook_for_sql()

# Using SQL From Other Programming Language

In [ ]:
!printf "CREATE DATABASE IF NOT EXISTS programming_examples" | mariadb

In [ ]:
%sql mysql:///programming_examples?unix_socket=/var/run/mysql/mysql.sock

## Operations on an SQL Database From Python

> PEP stands for Python Enhancement Proposal. A PEP is a design document providing information to the Python community, or describing a new feature for Python or its processes or environment. _(from [PEP 1](https://peps.python.org/pep-0001/))_

[PEP 249 – Python Database API Specification v2.0](https://peps.python.org/pep-0249/)

_notes_

In any sufficiently popular general purpose programming language, users of the language are going to start implementing interfaces to various databases.  As the number of libraries adding support for various DMBSes grows, it is beneficial for the language's community to have a consistent API for communicating with various database systems.  This decreases the learning and porting effort of programmers.

PEP 249 defines object types (even including exception types), methods, behavior, and variables.

In [ ]:
import MySQLdb

connection = MySQLdb.connect(
    database='programming_examples',
    unix_socket='/var/run/mysql/mysql.sock'
)

connection

_notes_     

https://peps.python.org/pep-0249/#connect

Parameters are database-specific, but some keywords (e.g., `user`, `password`, `host`, and `database`) are suggested.

In [ ]:
cursor = connection.cursor()

cursor

_notes_

https://peps.python.org/pep-0249/#cursor

Database queries are typically performed using cursors.  Cursor allows fetching query result in parts (which makes a lot of sense for big queries!).  Multiple cursors allow an application to perform other database operations without regard to queries that have been performed but are yet to have their last result row fetched.

In [ ]:
cursor.execute('DROP TABLE IF EXISTS follows')

_notes_

https://peps.python.org/pep-0249/#id19

The `Cursor.execute()` method accepts an operation that, in our case, can be a string with some SQL code.  An interface implementation can return whatever it wants from this method.  MySQLdb happens to return the number of rows fetched.

In [ ]:
cursor.execute('''
    DROP TABLE IF EXISTS users;

    CREATE TABLE users (
        id            INT PRIMARY KEY AUTO_INCREMENT,
        login         VARCHAR(50)    UNIQUE NOT NULL,
        password_salt VARBINARY(10)  UNIQUE NOT NULL,
        password_hash VARBINARY(130)        NOT NULL
    );

    CREATE TABLE follows (
        follower_id INT,
        followed_id INT,
        since       DATE NOT NULL,
        PRIMARY KEY (follower_id, followed_id),
        FOREIGN KEY (follower_id) REFERENCES users (id),
        FOREIGN KEY (followed_id) REFERENCES users (id),
        CHECK (follower_id <> followed_id)
    )
''')

_notes_

This is almost a subset of our git forge schema.  However, it resembles many possible kinds of platforms that have the notion of users who can log in and subscribe to others' profiles.

In [ ]:
import hashlib

def gen_salt():
    with open('/dev/random', 'rb') as random:
        return random.read(6)

def hash_password(salt, password):
    salted_password = salt + password.encode()
    return hashlib.md5(salted_password).digest()

In [ ]:
salt = gen_salt()

salt #.hex()

_notes_

Assume we are going to be adding new users to the db.  The application code should pick a random salt value for each user.

Try using the functions defined above to generate a salt and to hash some password with it.

In [ ]:
%%sql
SELECT X'deadbeef'

_notes_

We can obtain a string of arbitraty, non-ASCII bytes by using the (standard SQL) `X''` notation with a hexadecimal value between the apostrophes.

In [ ]:
import re

login_regex = re.compile('^[a-zA-Z_][a-zA-Z_0-9]+$')

def add_user(cursor, login, password):
    assert login_regex.match(login)
    salt = gen_salt()
    digest = hash_password(salt, password)
    command_string = f'''
        INSERT INTO users (login, password_salt, password_hash)
        VALUES ('{login}', X'{salt.hex()}', X'{digest.hex()}')
        RETURNING id
    '''
    cursor.execute(command_string)
    (new_id,) = cursor.fetchone()
    return new_id

_notes_

https://peps.python.org/pep-0249/#fetchone

In [ ]:
add_user(cursor, 'theodore', 'S3cur3 Pa$$word3')

_notes_

```python
add_user(cursor, 'pan_cratius', 'MUCH passw0rd, VERY secur!ty')
add_user(cursor, 'EUgenia', 'hack me, LOL!')
```

In [ ]:
%%sql
SELECT * FROM users

_notes_

```python
connection.commit()
```

https://peps.python.org/pep-0249/#commit

In [ ]:
cursor.execute('''
    INSERT INTO follows (followed_id, follower_id, since)
    VALUES (1, 2, NOW());
    INSERT INTO follows (followed_id, follower_id, since)
    VALUES (1, 3, NOW() - INTERVAL 1 DAY);
    INSERT INTO follows (followed_id, follower_id, since)
    VALUES (3, 2, NOW() - INTERVAL 2 DAY)
''')

In [ ]:
cursor.execute('SAVEPOINT my_checkpoint')
cursor.execute('''
    INSERT INTO follows (followed_id, follower_id, since)
    VALUES (3, 1, NOW() - INTERVAL 3 DAY);
''')
cursor.execute('ROLLBACK TO SAVEPOINT my_checkpoint')
cursor.execute('COMMIT')

_notes_

```python
cursor.execute('SAVEPOINT my_checkpoint')
cursor.execute('''
    INSERT INTO follows (followed_id, follower_id, since)
    VALUES (3, 1, NOW() - INTERVAL 2 DAY);
''')
cursor.execute('ROLLBACK TO SAVEPOINT my_checkpoint')
cursor.execute('COMMIT')
```

`COMMIT` also works when passed as text.

In [ ]:
%%sql
SELECT dst.login AS followed, src.login AS follower, since 
FROM users   src
JOIN follows     ON src.id = follows.follower_id
JOIN users   dst ON follows.followed_id = dst.id

### Unresolved Differences

In [ ]:
cursor.execute("SELECT CAST(X'deadbeef' AS BINARY)")
cursor.fetchone()

_notes_

```python
import psycopg2

psql_connection = psycopg2.connect(
    user = 'demo_user',
    password = 'demo_pwd',
    host = 'localhost',
    port = 25432,
    database = 'agh_it_northwind'
)

psql_cursor = sql_connection.cursor()

psql_cursor.execute("SELECT CAST(X'deadbeef' AS BINARY)")
psql_cursor.fetchall()
```

Postgres' closest type is `BYTEA`.

```python
psql_cursor.execute("SELECT CAST(X'deadbeef' AS BYTEA)")
```

Note the different returned type (`memoryview` rather than `bytes`).

## Prepared Statements

In [ ]:
%%sql
SELECT * FROM users

In [ ]:
def sign_in_interactive(cursor):
    login = input('login: ')
    password = input('password: ')

    query_string = f'''
        SELECT password_salt
        FROM users
        WHERE login = '{login}'
    '''
    cursor.execute(query_string)
    if cursor.rowcount == 0:
        return False
    (salt,) = cursor.fetchone()

    digest = hash_password(salt, password)

    query_string = f'''
        SELECT COUNT(*) > 0
        FROM users
        WHERE password_hash = X'{digest.hex()}' AND
              login = '{login}'
    '''
    cursor.execute(query_string)
    (result,) = cursor.fetchone()
    
    return bool(result)

_notes_

https://peps.python.org/pep-0249/#rownumber

In [ ]:
sign_in_interactive(cursor)

_notes_

```
login: theodore
password: S3cur3 Pa$$word3
```

Later, use `' OR TRUE -- ` as login.

Or `'; DROP TABLE follows; DROP TABLE users; COMMIT -- `, whatever.

In [ ]:
%%sql
PREPARE get_salt FROM
'SELECT password_salt
 FROM users
 WHERE login = ?'

In [ ]:
%%sql
EXECUTE get_salt USING 'theodore'

_notes_

```sql
DEALLOCATE PREPARE get_salt
```

Statements are allocated per-session, so they would get purge at the and of the session, anyway.  But for a long-running session with many statements created from dynamic data it might make a difference.

In [ ]:
%%sql
PREPARE verify_hash FROM
'SELECT COUNT(*) > 0
 FROM users
 WHERE password_hash = ? AND
       login = ?'

In [ ]:
%%sql
EXECUTE verify_hash USING X'deadbeef', 'pan_cratius'

### Using Prepared Statements From within Python

In [ ]:
def sign_in_interactive(cursor):
    login = input('login: ')
    password = input('password: ')

    query_string = f'''
        SELECT password_salt
        FROM users
        WHERE login = %s
    '''
    cursor.execute(query_string, (login,))
    if cursor.rowcount == 0:
        return False
    (salt,) = cursor.fetchone()

    digest = hash_password(salt, password)

    query_string = f'''
        SELECT COUNT(*) > 0
        FROM users
        WHERE password_hash = %s AND
              login = %s
    '''
    cursor.execute(query_string, (digest, login))
    (result,) = cursor.fetchone()
    
    return bool(result)

_notes_

Question marks are not used uniformly in parameterized statements in Python db interfaces.  PEP 249 [allows an implementation to choose](https://peps.python.org/pep-0249/#paramstyle) from a set of possible paramater marker types.

The interface implementation does not, in fact, have to use the prepared statements feature of the DBMS…

In [ ]:
sign_in_interactive(cursor)

_notes_

```
login: theodore
password: S3cur3 Pa$$word3
```

## In Other Programming Languages

- JDBC (not really "Java Database Connectivity" 😉)
- ODBC ("Open Database Connectivity", for C language)

_notes_

When Oracle failed to trademark "Java Database Connectivity", it started using the name "JDBC" exclusively, no more treating it as an acronym of something.

https://www.oracle.com/database/technologies/appdev/jdbc.html